#### Read the preprocessed data from a Parquet file into a DataFrame 'model_df', cache it for better performance and display its contents.

In [0]:
# Read dataset from checkpoint
model_df = spark.read.parquet("/tmp/project/preprocessed_data")
model_df.cache()

display(model_df)

id Body Title Tags text label id_dup true_labels tokens stop_words stemmed filtered cv features 10564355 I have a table named person_relation Id | ParentId | ChildId | PersonId ------------------------------------------- 1 | null | 2 | null ------------------------------------------- 2 | 1 | 3 | null ------------------------------------------- 3 | 2 | 4 | 122 ------------------------------------------- 4 | 3 | null | 122 ------------------------------------------- These 4 rows belong to one single person whose id is 122. I am struggling in updating the PersonId column; the first 2 rows should have 122 as PersonId. Id | ParentId | ChildId | PersonId ------------------------------------------- 1 | null | 2 | null ------------------------------------------- 2 | 1 | 3 | null ------------------------------------------- 3 | 2 | 4 | 122 ------------------------------------------- 4 | 3 | null | 122 ------------------------------------------- 5 | null | 6 | 123 ------------------------------------------- 6 | 5 | 7 | null ------------------------------------------- 7 | 6 | 8 | 123 ------------------------------------------- 8 | 7 | null | null ------------------------------------------- Now the table has two persons whose ids are 122 and 123. And it may have many persons in it. So the above replies wont work. Hence we need an iterative method to update these rows. Iterate and update table in SQL mysql iterate and update table in sql p i have a table named code person relation code p pre code id parentid childid personid 1 null 2 null 2 1 3 null 3 2 4 122 4 3 null 122 code pre p these 4 rows belong to one single person whose id is 122 i am struggling in updating the personid column the first 2 rows should have 122 as personid p hr pre code id parentid childid personid 1 null 2 null 2 1 3 null 3 2 4 122 4 3 null 122 5 null 6 123 6 5 7 null 7 6 8 123 8 7 null null code pre p now the table has two persons whose ids are 122 and 123 and it may have many persons in it so the above replies wont work hence we need an iterative method to update these rows p 10.0 10564355 List(10.0, 6.0) List(iterate, and, update, table, in, sql, p, i, have, a, table, named, code, person, relation, code, p, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 122, code, pre, p, these, 4, rows, belong, to, one, single, person, whose, id, is, 122, i, am, struggling, in, updating, the, personid, column, the, first, 2, rows, should, have, 122, as, personid, p, hr, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 122, 5, null, 6, 123, 6, 5, 7, null, 7, 6, 8, 123, 8, 7, null, null, code, pre, p, now, the, table, has, two, persons, whose, ids, are, 122, and, 123, and, it, may, have, many, persons, in, it, so, the, above, replies, wont, work, hence, we, need, an, iterative, method, to, update, these, rows, p) List(iterate, update, table, sql, p, table, named, code, person, relation, code, p, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 122, code, pre, p, 4, rows, belong, one, single, person, whose, id, 122, struggling, updating, personid, column, first, 2, rows, 122, personid, p, hr, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 122, 5, null, 6, 123, 6, 5, 7, null, 7, 6, 8, 123, 8, 7, null, null, code, pre, p, table, two, persons, whose, ids, 122, 123, may, many, persons, replies, wont, work, hence, need, iterative, method, update, rows, p) List(iter, updat, tabl, sql, p, tabl, name, code, person, relat, code, p, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 122, code, pre, p, 4, row, belong, one, singl, person, whose, id, 122, struggl, updat, personid, column, first, 2, row, 122, personid, p, hr, pre, code, id, parentid, childid, personid, 1, null, 2, null, 2, 1, 3, null, 3, 2, 4, 122, 4, 3, null, 1

#### Import Logistic Regression and set model parameters. Split the dataset, create, fit, and predict with Logistic Regression.


In [0]:
from pyspark.ml.classification import LogisticRegression

# Set parameters
max_iterations = 100
regularization_parameter = 0.0   # No improvement in performance with regularization
elastic_net_parameter = 0.0      # No improvement in performance with regularization

# Split the dataset
training_data, testing_data = model_df.randomSplit([0.9, 0.1], seed=32)
training_data = training_data.cache()

# Create and fit the Logistic Regression model
logistic_regression = LogisticRegression(maxIter=max_iterations, regParam=regularization_parameter, elasticNetParam=elastic_net_parameter)
model = logistic_regression.fit(training_data)

# Make predictions on the test data
predictions = model.transform(testing_data)

#### Import libraries, define UDF, generate predicted labels, prepare data, and transform labels for evaluation.


In [0]:
from sklearn.preprocessing import MultiLabelBinarizer
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, hamming_loss
from pyspark.sql.functions import udf
from pyspark.sql.types import ArrayType, StringType

# Define a UDF for extracting labels that exceed a specified probability threshold
@udf(ArrayType(StringType()))
def get_high_probability_labels(probabilities, threshold=0.2):
    return [str(i) for i, prob in enumerate(probabilities) if prob > threshold]

# Generate predicted labels by applying the UDF to the prediction probabilities
predictions_with_labels = predictions.withColumn("predicted_labels", get_high_probability_labels(predictions.probability))

# Select the true and predicted labels for evaluation
label_comparison_df = predictions_with_labels.select("true_labels", "predicted_labels")

# Initialize the MultiLabelBinarizer for transforming labels
label_binarizer = MultiLabelBinarizer()

# Convert Spark DataFrames to Pandas for compatibility with scikit-learn
true_labels_pd = model_df.toPandas()
predicted_labels_pd = predictions_with_labels.toPandas()

# Fit the binarizer to the true labels to establish the label mapping
label_binarizer.fit(true_labels_pd["true_labels"].apply(lambda labels: [int(label) for label in labels]))

# Transform the true and predicted labels into binary indicator arrays
binary_true_labels = label_binarizer.transform(predicted_labels_pd["true_labels"].apply(lambda labels: [int(label) for label in labels]))
binary_predicted_labels = label_binarizer.transform(predicted_labels_pd["predicted_labels"].apply(lambda labels: [int(label) for label in labels]))


##### Calculate evaluation metrics (accuracy, precision, recall, hamming loss) for the model's predictions and display the results.


In [0]:
# Calculate evaluation metrics
accuracy = accuracy_score(binary_true_labels, binary_predicted_labels)
precision = precision_score(binary_true_labels, binary_predicted_labels, average='micro')
recall = recall_score(binary_true_labels, binary_predicted_labels, average='micro')
hamming_loss_value = hamming_loss(binary_true_labels, binary_predicted_labels)

# Display evaluation results
print("Accuracy on the testing dataset:", accuracy)
print("Precision on the testing dataset:", precision)
print("Recall on the testing dataset:", recall)
print("Hamming Loss on the testing dataset:", hamming_loss_value)


Accuracy on the testing dataset: 0.006269592476489028
Precision on the testing dataset: 0.9817158931082982
Recall on the testing dataset: 0.6421343146274149
Hamming Loss on the testing dataset: 0.001074329145587634


#### Import libraries, read data, define parameters, and fit a Logistic Regression model.


In [0]:
from pyspark.ml.classification import LogisticRegression
from sklearn.preprocessing import MultiLabelBinarizer

# Read dataset from checkpoint
model_df = spark.read.parquet("/tmp/project/preprocessed_data")
model_df = model_df.cache()

#Parameters
maxIter = 100
regParam = 0.0
elasticNetParam = 0.0

# Define Logistic Regression model
lr = LogisticRegression(maxIter=maxIter, regParam=regParam, elasticNetParam=elasticNetParam)
lr_model = lr.fit(model_df)

##### Save the trained Logistic Regression model 'lr_model' to the specified location for temporary use in a deployment notebook.


In [0]:
# Save models temporarily for use in deployment notebook
lr_model.save('/mnt/mydatalakefilesystem/Capstone2/Models/lr_model')